# Hafta 10: LLM Tabanlı Sistem Mimarileri (LLMOps & Agents)

**Dersin Hedefleri:**
1.  Tekil LLM çağrılarının ötesine geçerek, birden çok adımdan oluşan karmaşık zincirler (chains) oluşturmayı öğrenmek.
2.  **Agent (Ajan)** kavramını ve bir LLM'in harici araçları (tools) otonom olarak nasıl kullanabildiğini anlamak.
3.  `LangChain` gibi bir framework'ün, LLM tabanlı uygulama geliştirmeyi nasıl basitleştirdiğini kavramak.
4.  **LLMOps** kavramını tanımak: Prompt yönetimi, LLM çıktılarının değerlendirilmesi ve maliyet takibi gibi LLM'e özgü operasyonel zorluklar.
5.  Basit bir "agent" prototipi oluşturmak.

## 1. Zincirlerden (Chains) Ajanlara (Agents)

Önceki haftalarda LLM'leri tek bir görev için kullandık (bir soruya cevap ver, metni özetle vb.). Ancak gerçek dünya problemleri genellikle birden çok adım gerektirir.

**Zincir (Chain):** Önceden tanımlanmış bir sırayla birden çok LLM çağrısını veya başka bileşenleri (API çağrıları, veri işleme adımları) birbirine bağlayan bir yapıdır.
*   **Örnek:** Bir makaleyi al -> İlk LLM çağrısı ile özetle -> İkinci LLM çağrısı ile özeti 3 maddelik bir listeye dönüştür -> Üçüncü LLM çağrısı ile bu listeyi sosyal medya postuna çevir.

**Ajan (Agent):** Bir zincirden daha gelişmiştir. Agent, sabit bir adımlar dizisini takip etmez. Bunun yerine, bir **hedefe** ulaşmak için hangi **araçları (tools)** hangi sırayla kullanacağına kendisi karar veren bir LLM tarafından yönetilen bir döngüdür.

**Agent'ın Düşünme Döngüsü (ReAct Prensibi):**
1.  **Reason (Düşün):** Verilen görev ve mevcut araçlar listesine bakarak bir sonraki adımın ne olması gerektiğine karar verir.
2.  **Act (Eyleme Geç):** Karar verdiği aracı, uygun parametrelerle çağırır.
3.  **Observe (Gözlemle):** Aracın döndürdüğü sonucu gözlemler.
4.  Bu gözlemi kullanarak tekrar 1. adıma döner ve hedefe ulaşana kadar bu döngüyü tekrarlar.

## 2. `LangChain` ile Uygulama Geliştirme

**LangChain**, LLM tabanlı uygulamalar geliştirmek için tasarlanmış açık kaynaklı bir framework'tür. Zincirler, ajanlar, RAG pipeline'ları ve harici araçlarla entegrasyon gibi karmaşık yapıları oluşturmak için standartlaştırılmış bileşenler sunar.

**Kurulum:**
```bash
pip install langchain langchain-openai
```

### Uygulama: Hava Durumu Sorabilen Bir Agent

Bu uygulamada, LLM'e yeni bir yetenek kazandıracağız: internetten gerçek zamanlı hava durumu bilgisi alabilme. Bunu, LLM'in kullanabileceği özel bir "araç" (tool) tanımlayarak yapacağız.

### 2.4 RAG + Agents: The Power Combination

En güçlü LLM sistemleri, **RAG** ve **Function Calling**'i birleştirir:

**Örnek Use Case: Akıllı Müşteri Destek**
```python
tools = [
    search_knowledge_base(),    # RAG: KB'den bilgi al
    get_user_data(),            # Function: CRM'den müşteri bilgisi
    create_ticket(),            # Function: Destek talebi oluştur
    check_order_status()        # Function: Sipariş durumu
]
```

**Kullanıcı:** "Siparişim nerede ve iade politikanız nedir?"

**Agent Akışı:**
1. `check_order_status()` → "Kargoda, yarın teslim"
2. `search_knowledge_base("iade politikası")` → "14 gün içinde iade"
3. Final yanıt: Her iki soruya da cevap verir

### 2.5 Production Best Practices

**✅ Yapılması Gerekenler:**
1. **Clear Tool Descriptions**: LLM'in doğru tool'u seçmesi için detaylı açıklamalar
2. **Error Handling**: Her tool try-except ile korunmalı
3. **Iteration Limits**: Sonsuz döngüyü önlemek için max_iterations
4. **Logging**: Her tool call'u logla (debugging için kritik)
5. **Cost Tracking**: API maliyetlerini izle

**❌ Yapılmaması Gerekenler:**
1. **Too Many Tools**: 10+ tool agent'ı karıştırır
2. **Unsafe Eval**: Kullanıcı input'unu direkt çalıştırma
3. **No Validation**: Tool sonuçlarını validate etmeden kullanma
4. **Stateless Agents**: Context'i koru (multi-turn conversations)

### 2.6 Agent Decision Patterns

**Pattern 1: Sequential** (A → B → C)
```
User: "Ankara ve Istanbul'daki hava farkı nedir?"
Agent: get_weather("Ankara") → get_weather("Istanbul") → calculate("12-18") → Answer
```

**Pattern 2: Conditional** (if-then)
```
User: "Ankara soğuksa İstanbul'u da söyle"
Agent: get_weather("Ankara") → [if temp < 15] → get_weather("Istanbul") → Answer
```

**Pattern 3: Parallel** (A || B)
```
User: "Hem hava hem de döviz kuru"
Agent: [get_weather() || get_exchange_rate()] → Answer
```

# Usage Examples: Agent in Action
# 
# ⚠️ ÖNCE ÖNCEKİ HÜCRELERİ ÇALIŞTIRIN:
#    1. Setup cell (tool definitions)
#    2. Helper function cell (run_agent definition)

print("="*80)
print("AGENT EXAMPLES - Function Calling ile LLM")
print("="*80)

# Example 1: Basit hava durumu sorgusu
print("\n[Example 1] Basit tool kullanımı")
print("-"*80)
response1 = run_agent("Istanbul'daki hava durumu nasıl?")
print(response1)

# Example 2: Çoklu adım - hesaplama gerektiren
print("\n\n[Example 2] Çoklu tool kullanımı")
print("-"*80)
response2 = run_agent("Ankara'daki sıcaklığı 2 ile çarp, sonucu söyle")
print(response2)

# Example 3: Birden fazla şehir karşılaştırma
print("\n\n[Example 3] Karmaşık reasoning")
print("-"*80)
response3 = run_agent("Istanbul ve Ankara'daki hava durumunu karşılaştır, hangisi daha sıcak?")
print(response3)

print("\n" + "="*80)

# Helper Function: Simple Agent Loop

def run_agent(user_message, model="gemini/gemini-pro", max_iterations=5, verbose=True):
    """
    Basit bir agent döngüsü: LLM'e soru sor, tool çağırsın, sonucu kullan
    
    Args:
        user_message: Kullanıcı sorusu
        model: LiteLLM model tag (default: gemini/gemini-pro)
        max_iterations: Maksimum tool çağrı sayısı
        verbose: Ara adımları göster
    
    Returns:
        LLM'in final cevabı
    """
    messages = [{"role": "user", "content": user_message}]
    
    for i in range(max_iterations):
        # LLM'i çağır
        response = completion(
            model=model,
            messages=messages,
            tools=tools,
            temperature=0.0
        )
        
        response_message = response.choices[0].message
        
        # Tool çağrısı var mı?
        if hasattr(response_message, 'tool_calls') and response_message.tool_calls:
            if verbose:
                print(f"\n🤖 Agent Iteration {i+1}")
            
            # Assistant'ın mesajını kaydet
            messages.append({
                "role": "assistant",
                "content": response_message.content,
                "tool_calls": [
                    {
                        "id": tc.id,
                        "type": tc.type,
                        "function": {
                            "name": tc.function.name,
                            "arguments": tc.function.arguments
                        }
                    }
                    for tc in response_message.tool_calls
                ]
            })
            
            # Her tool'u çalıştır
            for tool_call in response_message.tool_calls:
                func_name = tool_call.function.name
                func_args = json.loads(tool_call.function.arguments)
                
                if verbose:
                    print(f"  🔧 Calling: {func_name}({func_args})")
                
                # Tool'u çalıştır
                try:
                    result = tool_functions[func_name](**func_args)
                    if verbose:
                        print(f"  ✓ Result: {result}")
                except Exception as e:
                    result = json.dumps({"error": str(e)})
                    if verbose:
                        print(f"  ❌ Error: {result}")
                
                # Tool sonucunu ekle
                messages.append({
                    "role": "tool",
                    "tool_call_id": tool_call.id,
                    "name": func_name,
                    "content": result
                })
        
        # Final cevap
        elif response_message.content:
            if verbose:
                print(f"\n✅ Final Answer:")
            return response_message.content
        
        else:
            return "Model yanıt vermedi"
    
    return "Maksimum iterasyon sayısına ulaşıldı"

print("✓ Helper function 'run_agent()' tanımlandı")

# Setup: LiteLLM ile Function Calling

!pip install -q litellm

import json
import os
from litellm import completion

# API Key setup
GEMINI_API_KEY = os.getenv("GEMINI_API_KEY")
if not GEMINI_API_KEY:
    from getpass import getpass
    GEMINI_API_KEY = getpass("GEMINI_API_KEY girin: ")
    os.environ["GEMINI_API_KEY"] = GEMINI_API_KEY

# ============================================================================
# Tool Implementations (Gerçek API'lere bağlanabilir)
# ============================================================================

def get_current_weather(location: str, unit: str = "celsius") -> str:
    """Simulated weather API"""
    weather_db = {
        "istanbul": {"temp_c": 18, "condition": "Partly cloudy"},
        "ankara": {"temp_c": 12, "condition": "Sunny"},
        "izmir": {"temp_c": 22, "condition": "Clear"},
    }
    
    location_key = location.lower().replace("ı", "i")
    data = weather_db.get(location_key, {"temp_c": 20, "condition": "Unknown"})
    
    temp = data["temp_c"]
    if unit == "fahrenheit":
        temp = (temp * 9/5) + 32
    
    return json.dumps({
        "location": location,
        "temperature": temp,
        "unit": unit,
        "condition": data["condition"]
    })


def calculate(expression: str) -> str:
    """Safe mathematical calculation"""
    try:
        allowed_chars = set("0123456789+-*/(). ")
        if not all(c in allowed_chars for c in expression):
            return json.dumps({"error": "Invalid characters"})
        
        result = eval(expression)
        return json.dumps({"expression": expression, "result": result})
    except Exception as e:
        return json.dumps({"error": str(e)})


# ============================================================================
# Tool Definitions (LLM'in anlayacağı format)
# ============================================================================

tools = [
    {
        "type": "function",
        "function": {
            "name": "get_current_weather",
            "description": "Get current weather for a specific location",
            "parameters": {
                "type": "object",
                "properties": {
                    "location": {
                        "type": "string",
                        "description": "City name, e.g., Istanbul, Ankara"
                    },
                    "unit": {
                        "type": "string",
                        "description": "Temperature unit: celsius or fahrenheit",
                        "enum": ["celsius", "fahrenheit"]
                    }
                },
                "required": ["location"]
            }
        }
    },
    {
        "type": "function",
        "function": {
            "name": "calculate",
            "description": "Evaluate a mathematical expression",
            "parameters": {
                "type": "object",
                "properties": {
                    "expression": {
                        "type": "string",
                        "description": "Math expression, e.g., '25 * 3' or '100 / 4'"
                    }
                },
                "required": ["expression"]
            }
        }
    }
]

# Tool registry: function name -> Python function
tool_functions = {
    "get_current_weather": get_current_weather,
    "calculate": calculate
}

print("✓ Setup complete!")
print(f"✓ Available tools: {list(tool_functions.keys())}")

---

## 2. Function Calling: LLM'lere Araç Kullanma Yeteneği

Hafta 9'da function calling'in temellerini gördük. Şimdi production-ready agent'lar oluşturacağız.

### 2.1 Agent Mimarisi

**Agent = LLM + Tools + Decision Loop**

```
┌─────────────────────────────────────────┐
│  1. User Query                           │
└──────────────┬──────────────────────────┘
               ↓
┌─────────────────────────────────────────┐
│  2. LLM Reasoning (ReAct Pattern)       │
│     "I need to call get_weather()"       │
└──────────────┬──────────────────────────┘
               ↓
┌─────────────────────────────────────────┐
│  3. Execute Tool                         │
│     → get_weather("Istanbul")            │
│     → Result: "18°C, cloudy"            │
└──────────────┬──────────────────────────┘
               ↓
┌─────────────────────────────────────────┐
│  4. LLM Synthesis                        │
│     "The weather in Istanbul is..."      │
└─────────────────────────────────────────┘
```

### 2.2 Tool Declaration vs Implementation

**Key Design Pattern:**
- **Declaration**: JSON Schema (LLM'e ne yapabileceğini söyler)
- **Implementation**: Python function (gerçek işi yapar)
- **Registry**: Mapping (declaration → implementation)

# BONUS: LangChain ile Agent (Opsiyonel)
# 
# LangChain gibi framework'ler daha karmaşık agent sistemleri için kullanışlıdır.
# Yukarıdaki basit implementation çoğu use case için yeterlidir.
#
# LangChain kullanmak isterseniz:
# !pip install langchain langchain-openai
#
# from langchain.agents import tool, AgentExecutor, create_react_agent
# from langchain import hub
# from langchain_openai import ChatOpenAI
#
# @tool
# def get_weather(city: str) -> str:
#     """Bir şehrin hava durumunu döndürür"""
#     return f"{city} için hava durumu: 20°C, güneşli"
#
# tools = [get_weather]
# llm = ChatOpenAI(model="gpt-4")
# prompt = hub.pull("hwchase17/react")
# agent = create_react_agent(llm, tools, prompt)
# agent_executor = AgentExecutor(agent=agent, tools=tools, verbose=True)
# agent_executor.invoke({"input": "Ankara'daki hava durumu nasıl?"})

print("✓ LangChain örneği - gerçek kullanım için yorum satırlarını kaldırın")

### Yukarıdaki Akışın Açıklaması

`agent_executor.invoke` çağrıldığında arka planda şunlar olur:

1.  **İlk LLM Çağrısı:** LangChain, kullanıcı sorusunu (`Ankara'daki hava durumu nasıl?`) ve kullanılabilecek araçların listesini (`get_weather` aracının açıklaması) birleştirerek LLM için bir prompt oluşturur.
2.  **LLM'in Kararı (Reason & Act):** Bizim `MockChatLLM`'imiz, bu prompt'u aldığında, sorunun hava durumuyla ilgili olduğunu anlar ve `get_weather` aracını kullanması gerektiğine karar verir. Çıktı olarak `Action: get_weather, Action Input: {"city": "Ankara"}` metnini üretir.
3.  **LangChain Aracı Çağırır:** LangChain, bu çıktıyı ayrıştırır, `get_weather` fonksiyonunu `"Ankara"` parametresiyle çağırır.
4.  **Gözlem (Observe):** `get_weather` fonksiyonu `"Hava durumu Ankara'da 25 C ve güneşli."` sonucunu döndürür. Bu, "Observation" (gözlem) olarak adlandırılır.
5.  **İkinci LLM Çağrısı:** LangChain, bu gözlemi alıp, LLM için yeni bir prompt oluşturur: `"...Observation: Hava durumu Ankara'da 25 C ve güneşli. ..."`
6.  **LLM'in Nihai Cevabı:** LLM, bu gözleme bakarak artık soruyu cevaplayabileceğini anlar ve `Final Answer: Ankara'da hava 25 derece ve güneşli.` çıktısını üretir.
7.  Agent döngüsü durur ve bu nihai cevap kullanıcıya gösterilir.

## 4. LLMOps: LLM'e Özgü Operasyonel Zorluklar

LLM tabanlı uygulamaları üretime almak, geleneksel MLOps'a ek olarak yeni zorluklar getirir.

- **Prompt Yönetimi (Prompt Management):** Prompt'lar artık projenin en kritik parçalarından biridir. Onları kod gibi versiyonlamak, A/B testine tabi tutmak ve performanslarını izlemek gerekir.
- **Çıktı Değerlendirmesi:** LLM çıktılarının "doğruluğunu" ölçmek zordur. Geleneksel metrikler (accuracy) genellikle yetersizdir. Bunun yerine, "Helpfulness" (Yardımcılık), "Correctness" (Doğruluk) gibi metrikler için başka bir LLM'i değerlendirici olarak kullanma (LLM-as-a-Judge) gibi teknikler popülerleşmektedir.
- **Maliyet ve Gecikme (Cost & Latency):** API çağrıları maliyetlidir ve gecikme süresi yüksek olabilir. Sık kullanılan istekler için bir önbellekleme (caching) mekanizması kurmak genellikle zorunludur.
- **Güvenlik:** Kötü niyetli kullanıcılar, "prompt injection" gibi tekniklerle agent'ınıza istemediğiniz komutları verdirmeye çalışabilirler.

### Alıştırma: Agent'a Yeni Bir Araç Ekleme

1.  Basit bir Python fonksiyonu olarak `calculate_len` adında yeni bir `@tool` tanımlayın. Bu araç, bir string almalı ve o string'in karakter sayısını döndürmelidir. Docstring'i, aracın ne işe yaradığını açıkça belirtmelidir (örn: `"Bir metnin uzunluğunu karakter olarak hesaplamak için kullanılır."`).
2.  Bu yeni aracı, `tools` listesine ekleyin.
3.  `agent_executor`'ı `"Merhaba kelimesi kaç harften oluşur?"` gibi bir soruyla çağırın.
4.  Agent'ın, doğru aracı (`calculate_len`) seçip, doğru parametreyle (`"Merhaba"`) çağırıp, dönen sonucu kullanıcıya sunduğunu gözlemleyin. (Bunun için `MockChatLLM`'in mantığını bu yeni senaryoyu da içerecek şekilde genişletmeniz gerekebilir).